In [8]:
import gensim
import MySQLdb
import csv

# initializing the titles and rows list 
fields = [] 
rows = [] 
raw_questions = []

filename = 'contributions.csv'
# reading csv file 
with open(filename, 'r', encoding="utf8") as csvfile: 
    # creating a csv reader object 
    csvreader = csv.reader(csvfile) 
      
    # extracting field names through first row 
    fields = next(csvreader) 
  
    # extracting each data row one by one 
    for row in csvreader: 
        rows.append(row) 
  
    # get total number of rows 
#     print("Total no. of rows: %d"%(csvreader.line_num)) 
    
    # printing the field names 
#     print('Field names are:' + ', '.join(field for field in fields)) 

    #  printing first 5 rows 
#     print('\nFirst 5 rows are:\n') 

    curr_question = ""
    curr_text = ""
    curr_topic = ""
    curr_folder = ""
    curr_answer = ""
    curr_number = 0
    curr_follow_up = 0
    endorsed = 0
    
    # This will help us take the most recent version because it always comes first
    already_filled = 0
    for row in rows[:]: 
        # parsing each column of a row 
        for col,field in zip(row, fields): 
            if(field == "Post Number" and curr_number != int(col)):
                if(curr_question != "" and curr_answer != ""):
                    #update_at_signs(curr_answer)
                    #sql = "INSERT INTO CIS120 (question_number, subject, topic, question, answer, num_times_referred_to, "\
                    #"follow_up_number, endorsed) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)" 
                    #val = (int(curr_number), curr_folder, curr_topic, curr_question, curr_answer, int(0), int(curr_follow_up), int(endorsed))
                    # myDB.execute(sql, val)
                    raw_questions.append(curr_question)
                curr_number = int(col)
                curr_follow_up = 0
                curr_question = ""
                already_filled = 0
                curr_answer = ""
                curr_topic = ""
                endorsed = 0
                
            elif(field == "Submission HTML Removed"): #the question could also be in subject
                curr_text = col
                
            elif(field == "Subject"): #We want to check if this is actually the question eventaully
                curr_topic = col
                
            elif(field == "Folders"):
                curr_folder = col
                
            elif(field == "Endorsed by Instructor"):
                if(col == "TRUE"):
                    endorsed = 1
                else:
                    endorsed = 0
            elif(field == "Part of Post"):
                if(col == "started_off_question"):
                    if(already_filled == 0):
                        curr_question = curr_text
                    already_filled = 0
                elif(col == "updated_question"):
                    # update question entry to post and follow up numbers
                    if(already_filled == 0):
                        curr_question = curr_text
                        already_filled = 1
                        
                elif(col == "updated_i_answer"):
                    # update last entry to the post and follow up number
                    # what if it was appended? how do we update just the end?
                    if(already_filled == 0):
                        curr_answer = curr_answer + "\n" + curr_text
                        already_filled = 1
                    endorsed = 1
                elif(col == "started_off_i_answer"):
                    if(already_filled == 0):
                        curr_answer = curr_answer + "\n" + curr_text
                    already_filled = 0
                    endorsed = 1
                    
                elif(col == "updated_s_answer"):
                    # update last entry to the post and follow up number
                    # what if it was appended? how do we update just the end?
                    if(already_filled == 0):
                        curr_answer = curr_answer + "\n" + curr_text
                        already_filled = 1
                elif(col == "started_off_s_answer"):
                    # append to answer - if it was previously endorsed and were appending should we keep it endorsed?
                    if(already_filled == 0):
                        curr_answer = curr_answer + "\n" + curr_text
                    already_filled = 0
                    
                elif(col == "followup"):
                    # new entry for the new followup question 
                    if(curr_question != ""):
                        #update_at_signs(curr_answer)
                        #sql = "INSERT INTO CIS120 (question_number, subject, topic, question, answer, num_times_referred_to, "\
                        #"follow_up_number, endorsed) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)" 
                        #val = (int(curr_number), curr_folder, curr_topic, curr_question, curr_answer, int(0), int(curr_follow_up), int(endorsed))
                        # myDB.execute(sql, val)
                        raw_questions.append(curr_question)
                        curr_question = ""
                        curr_answer = ""
                        endorsed = 0
                        already_filled = 0
                        
                    curr_follow_up = curr_follow_up + 1
                    curr_question = curr_text
                elif(col == "reply_to_followup"):
                    curr_answer = curr_answer + "\n" + curr_text
                    
                

# print(dir(gensim))

# see https://www.oreilly.com/learning/how-do-i-compare-document-similarity-using-python


#myDB = MySQLdb.connect(host="seniordesign.cbvhmgr3ve3r.us-east-2.rds.amazonaws.com",port=3306,user="grlpwr",passwd="ourseniordesignproject",db="seniordesign")
#cursor = myDB.cursor()
#query = "SELECT question FROM CIS120"
#cursor.execute(query)
#print(cursor.fetchall())

#for row in cursor.fetchall():
    #print(row[0])
    #raw_questions.append(row[i])
    
    
print("Number of questions:", len(raw_questions))

#myDB.close()


Number of questions: 5629


In [13]:
import nltk

# turn document into the list of tokens
from nltk.tokenize import word_tokenize
gen_docs = [[w.lower() for w in word_tokenize(text)] 
            for text in raw_questions]
print(gen_docs)

# create dictionary from list of documents 
dictionary = gensim.corpora.Dictionary(gen_docs)
print(dictionary[5])
print(dictionary.token2id['midterm'])
print("Number of words in dictionary:",len(dictionary))
for i in range(len(dictionary)):
    print(i, dictionary[i])
    
# create corpus for each document
corpus = [dictionary.doc2bow(gen_doc) for gen_doc in gen_docs]
print(corpus)

# create tf-idf model
tf_idf = gensim.models.TfidfModel(corpus)
print(tf_idf)
s = 0
for i in corpus:
    s += len(i)
print(s)

# create similarity measure object
sims = gensim.similarities.Similarity('/usr/workdir/',tf_idf[corpus],
                                      num_features=len(dictionary))
print(sims)
print(type(sims))

# create query document and turn it into tf-idf
query_doc = [w.lower() for w in word_tokenize("How does style grading work.")]
print(query_doc)
query_doc_bow = dictionary.doc2bow(query_doc)
print(query_doc_bow)
query_doc_tf_idf = tf_idf[query_doc_bow]
print(query_doc_tf_idf)

# array of document similarities to query
sims[query_doc_tf_idf]


[['i', 'wanted', 'to', 'switch', 'my', 'recitation', 'from', '212', 'to', '218', 'in', 'order', 'to', 'sign', 'up', 'for', 'another', 'class', '.', 'i', 'filled', 'out', 'the', 'form', 'on', 'the', 'cis', '120', 'website', '.', 'am', 'i', 'also', 'allowed', 'to', 'switch', 'it', 'in', 'pennintouch', 'so', 'that', 'i', 'can', 'sign', 'up', 'for', 'the', 'other', 'course', '?', 'thanks', ',', 'josh', 'cohen'], ['professor', ',', 'thanks', 'for', 'letting', 'me', 'know', '.', 'unfortunately', ',', 'since', 'i', 'had', "n't", 'heard', 'anything', 'and', 'i', 'wanted', 'to', 'make', 'sure', 'i', 'got', 'the', 'class', 'materials/homework', 'for', 'the', 'other', 'class', ',', 'i', 'switched', 'the', 'recitations', 'on', 'pennintouch', '.', 'i', 'specifically', 'chose', '218', 'since', 'it', 'was', 'listed', 'on', 'the', 'lecture', 'notes', 'as', 'needing', 'more', 'students', '.', 'is', 'there', 'any', 'way', 'i', 'can', 'keep', 'this', 'recitation', 'so', 'i', 'do', "n't", 'have', 'to', 's

?
2778
Number of words in dictionary: 11247
0 ,
1 .
2 120
3 212
4 218
5 ?
6 allowed
7 also
8 am
9 another
10 can
11 cis
12 class
13 cohen
14 course
15 filled
16 for
17 form
18 from
19 i
20 in
21 it
22 josh
23 my
24 on
25 order
26 other
27 out
28 pennintouch
29 recitation
30 sign
31 so
32 switch
33 thanks
34 that
35 the
36 to
37 up
38 wanted
39 website
40 'm
41 all
42 and
43 any
44 anything
45 as
46 back
47 chose
48 do
49 drop
50 got
51 had
52 have
53 heard
54 help
55 if
56 is
57 keep
58 know
59 lecture
60 letting
61 listed
62 make
63 materials/homework
64 me
65 more
66 n't
67 needing
68 not
69 notes
70 of
71 original
72 professor
73 really
74 recitations
75 since
76 sorry
77 specifically
78 students
79 sure
80 switched
81 temporarily
82 there
83 this
84 trouble
85 unfortunately
86 was
87 way
88 will
89 your
90 01
91 after
92 before
93 codio
94 complete
95 could
96 first
97 folder
98 hi
99 homework
100 just
101 need
102 or
103 our
104 please
105 saw
106 sheth
107 we
108 whether
109 wond

858 majorly
859 messing
860 notice
861 occurs
862 paste
863 placement
864 previous
865 reads
866 reason
867 reopen
868 running
869 sam
870 save
871 saved
872 separate
873 session
874 submission
875 telling
876 text
877 ts
878 w
879 worry
880 0-3
881 285
882 week
883 ahead
884 nice
885 +
886 dir
887 forward
888 limit
889 limits
890 method
891 move_robot
892 num_moves
893 pos
894 position
895 robot
896 setting
897 stopping
898 struggling
899 thus
900 y
901 initial
902 ^
903 concatenate
904 ex
905 expecting
906 giving
907 plus
908 returning
909 returns
910 string1
911 string2
912 strings
913 //try.ocamlpro.com/
914 entire
915 evaluate
916 following
917 helps
918 hope
919 returned
920 simplelisttostring
921 suspect
922 yes
923 list_one
924 list_two
925 themselves
926 false
927 falsey
928 meaning
929 true
930 advice
931 calculates
932 ensuring
933 evaluating
934 greater
935 hw12
936 length
937 main
938 size
939 thinking
940 zero
941 penalized
942 suggests
943 :tail
944 begin
945 end
946 mat

2177 |_
2178 *any*
2179 capture
2180 computed
2181 refractoring
2182 denoted
2183 somewhere
2184 262
2185 comment
2186 messy
2187 triplet_of_helix
2188 lnodes
2189 claims
2190 generic
2191 gagaaaaa
2192 e.g
2193 fed
2194 :ll
2195 prepend
2196 retrieve
2197 retrieves
2198 sides
2199 further
2200 performed
2201 recurse
2202 subtree
2203 specification
2204 tested
2205 higher
2206 brackets
2207 three
2208 //www.cis.upenn.edu/~cis120/current/hw/hw02/
2209 7c3
2210 closely
2211 differently
2212 http
2213 luckily
2214 related
2215 surprised
2216 white-cheeked
2217 aaaaaaaa
2218 aaactaga
2219 aaagaaaa
2220 agatct
2221 continuously
2222 ctaga
2223 contents
2224 differentiate
2225 singletons
2226 stating
2227 guessed
2228 sub
2229 0.0
2230 10.0
2231 11.2
2232 15.0
2233 18
2234 20
2235 20.0
2236 2017
2237 4pm
2238 5.0
2239 57
2240 86.2
2241 ancestors
2242 brandon
2243 chains
2244 decode
2245 dorothy
2246 finding
2247 hd=hd2
2248 hw02
2249 namestatushw02-submit.zip
2250 overall
2251 phylogenetic
2

2927 leaning
2928 safer
2929 situations
2930 :x
2931 circuits
2932 list.sort
2933 generics
2934 efficiently
2935 instructed
2936 leverage
2937 accomplish
2938 maintain
2939 maintaining
2940 funciton
2941 enclosed
2942 messages
2943 testset
2944 near
2945 brief
2946 hints
2947 declaration
2948 represented
2949 disperse
2950 runtest
2951 cutting
2952 truncates
2953 simpler
2954 explanation
2955 halfway
2956 throws
2957 re-order
2958 succinctly
2959 deduction
2960 recognized
2961 im
2962 vocab
2963 unorderedness
2964 non-duplicates
2965 behind
2966 concept
2967 int=
2968 series
2969 00:00
2970 :00.
2971 bui
2972 drink-connect
2973 er.native
2974 higherord
2975 higherorder.native
2976 ine
2977 lding
2978 moments
2979 refresh
2980 advised
2981 modifying
2982 catches
2983 loophole
2984 guys
2985 inserting
2986 represent
2987 adapt
2988 easy
2989 likewise
2990 exponentiation
2991 float
2992 float_of_int
2993 int_of_float
2994 conjunction
2995 .equals
2996 immediately
2997 is_empty
2998 stops


...

9675 component-
9676 hangman
9677 i/o-
9678 pick
9679 re-used
9680 testable
9681 topics
9682 winning
9683 forbidden
9684 freeze
9685 mario
9686 objective
9687 pieces
9688 platformer
9689 platforms
9690 tetris
9691 //www.instructables.com/id/making-a-basic-3d-engine-in-java/
9692 3-d
9693 engine
9694 raycasting
9695 tutorial
9696 medication
9697 prescribed
9698 scheduled
9699 wears
9700 animations
9701 toward
9702 ai
9703 alpha-beta
9704 chess
9705 minimax
9706 pruning
9707 adequate
9708 basis
9709 defenders
9710 defense
9711 deffender
9712 gameobj
9713 tower
9714 features
9715 punished
9716 *exact*
9717 external
9718 kryonet
9719 layer
9720 libgdx
9721 lwjgl
9722 networking
9723 rendering
9724 proposals
9725 sub-types
9726 triangles
9727 linked/recursive
9728 //www.pacxon4u.com/space-invaders/
9729 classic
9730 invaders
9731 uninitiated
9732 diamonds
9733 eat
9734 sushi
9735 collisions
9736 frogger
9737 aspects
9738 balls
9739 brickbreaker
9740 existence
9741 inheritance/2d
9742 inheri

10424 redudant
10425 'final
10426 /*
10427 //joingame
10428 //panes.setlocation
10429 actionperformed
10430 blackjack
10431 borderlayout.south
10432 control_panel
10433 control_panel.add
10434 court.doubledown
10435 court.hit
10436 court.reset
10437 court.split
10438 court.stand
10439 dollars
10440 doubledown
10441 doubledown.addactionlistener
10442 frame.pack
10443 frame.setdefaultcloseoperation
10444 frame.setlocation
10445 hit.addactionlistener
10446 jframe.exit_on_close
10447 joingame
10448 joptionpane.showconfirmdialog
10449 newname
10450 newname.equals
10451 newuser
10452 overridden
10453 p.getdollars
10454 p.getstartingdollars
10455 panes
10456 privately
10457 profit
10458 questions.pack
10459 questions.setlocation
10460 questions.setvisible
10461 returninguser
10462 split.addactionlistener
10463 stand.addactionlistener
10464 status_panel.add
10465 updateuserdata
10466 user_info
10467 users.containskey
10468 users.get
10469 users.put
10470 addlast
10471 enemygrid
10472 enemygrid

11174 bag.containskey
11175 bag.get
11176 inv1
11177 worthy
11178 circumstances
11179 mini-courses
11180 sem
11181 propagated
11182 routing
11183 //www.seas.upenn.edu/~cis120/current/exams/final-16fa-solutions.pdf
11184 12,000
11185 segmentlengths
11186 segmentvalues
11187 delegate
11188 byte
11189 *answer*
11190 *question*
11191 bettt
11192 thorugh
11193 counterexample
11194 reproduced
11195 hel
11196 lo
11197 whys
11198 cares
11199 haves
11200 bethany
11201 ceque
11202 exhaust
11203 bag.remove
11204 re-add
11205 command.type.create
11206 mesg
11207 frib
11208 j.frib
11209 base.hasnext
11210 base.next
11211 doubler
11212 non-null
11213 i.hasnext
11214 i.next
11215 l.add
11216 l.iterator
11217 test2
11218 x.equals
11219 x.getclass
11220 y.getclass
11221 -why
11222 actionperformedmethod
11223 button.addactionlistener
11224 illustrated
11225 inc
11226 pushed
11227 _______
11228 _______arraylist
11229 _______boolean_________
11230 ____arraylist
11231 ___string______________
11232 x.contai

TfidfModel(num_docs=5629, num_nnz=204646)
204646
Similarity index with 5629 documents in 0 shards (stored under /usr/workdir/)
<class 'gensim.similarities.docsim.Similarity'>
['how', 'does', 'style', 'grading', 'work', '.']
[(1, 1), (119, 1), (176, 1), (345, 1), (442, 1), (2811, 1)]
[(1, 0.06664919669217262), (119, 0.22023549025226244), (176, 0.2157786648835218), (345, 0.5121975654732246), (442, 0.36288338886574273), (2811, 0.711662195991423)]


FileNotFoundError: [Errno 2] No such file or directory: '/usr/workdir\\.0'